In [1]:
import os
import cv2
import json
import random
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

In [2]:
r1 = 'r1/'
r3 = 'r3/'
r5 = 'r5/'
r7 = 'r7/'

In [3]:
len(os.listdir(r1)), len(os.listdir(r3)), len(os.listdir(r5)), len(os.listdir(r7))

(3719, 3644, 3541, 3462)

In [4]:
3719+3644+3541+3462

14366

In [6]:
len(json.load(open('/data1/wangqiurui/code/datasets/rebuild/combined.json')).keys())

377

In [15]:
# check videos length
vl = []
for i in os.listdir(r1):
    cap = cv2.VideoCapture(r1+i)
    vl.append(int(cap.get(cv2.CAP_PROP_FRAME_COUNT))/30)
    cap.release()
np.array(vl).mean(), np.array(vl).std(), np.array(vl).max(), np.array(vl).min()

(63.93830778883212, 55.375124300686295, 489.1666666666667, 3.1666666666666665)

In [14]:
(np.array(vl) == 489.1666666666667).argmax()

3203

In [16]:
vl3 = []
for i in os.listdir(r3):
    cap = cv2.VideoCapture(r3+i)
    vl3.append(int(cap.get(cv2.CAP_PROP_FRAME_COUNT))/30)
    cap.release()
np.array(vl3).mean(), np.array(vl3).std(), np.array(vl3).max(), np.array(vl3).min()

(149.58121112330772, 94.78578381198311, 804.4333333333333, 14.9)

In [17]:
vl5 = []
for i in os.listdir(r5):
    cap = cv2.VideoCapture(r5+i)
    vl5.append(int(cap.get(cv2.CAP_PROP_FRAME_COUNT))/30)
    cap.release()
np.array(vl5).mean(), np.array(vl5).std(), np.array(vl5).max(), np.array(vl5).min()

(259.1039348583263, 119.82853583671516, 1127.0333333333333, 52.86666666666667)

In [18]:
vl7 = []
for i in os.listdir(r7):
    cap = cv2.VideoCapture(r7+i)
    vl7.append(int(cap.get(cv2.CAP_PROP_FRAME_COUNT))/30)
    cap.release()
np.array(vl7).mean(), np.array(vl7).std(), np.array(vl7).max(), np.array(vl7).min()

(373.8921528981321, 142.46022408658374, 1317.4, 89.33333333333333)

In [23]:
vl7.index(1317.4)

213

In [26]:
va = []
for i in [r1, r3, r5, r7]:
    for j in os.listdir(i):
        cap = cv2.VideoCapture(i+j)
        fps = cap.get(cv2.CAP_PROP_FPS)
        va.append(cap.get(cv2.CAP_PROP_FRAME_COUNT)/fps)
        cap.release()
np.array(va).mean(), np.array(va).std(), np.array(va).max(), np.array(va).min()

(208.46179637106133, 158.1661882039413, 1317.4, 3.1666666666666665)

In [22]:
va.index(3.1666666666666665)

1248

# combine thumos14

In [8]:
def combine_files(test_dir, val_dir, output_dir):
    # 检查输出目录是否存在，如果不存在则创建
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)
    
    # 存储test和val文件的字典
    test_files = {f[:-9]: f for f in os.listdir(test_dir) if f.endswith('_test.txt')}
    val_files = {f[:-8]: f for f in os.listdir(val_dir) if f.endswith('_val.txt')}

    # 遍历test文件字典
    for base_name, test_file in test_files.items():
        # 检查是否有对应的val文件
        if base_name in val_files:
            # 打开合并后的文件
            with open(os.path.join(output_dir, f'{base_name}.txt'), 'w') as outfile:
                # 读取并写入test文件内容
                with open(os.path.join(test_dir, test_file), 'r') as f:
                    outfile.write(f.read())
                
                # 读取并写入val文件内容
                with open(os.path.join(val_dir, val_files[base_name]), 'r') as f:
                    outfile.write(f.read())

                print(f'Combined file {base_name}.txt created in {output_dir}.')

# 路径定义
test_dir = '/data1/wangqiurui/code/datasets/rebuild/TH14_Temporal_Annotations_Test/annotations/annotation/'
val_dir = '/data1/wangqiurui/code/datasets/rebuild/TH14_Temporal_annotations_validation/annotation/'
output_dir = '/data1/wangqiurui/code/datasets/rebuild/thumos/'  # 新的输出目录

# 使用示例
combine_files(test_dir, val_dir, output_dir)


Combined file SoccerPenalty.txt created in /data1/wangqiurui/code/datasets/rebuild/thumos/.
Combined file ThrowDiscus.txt created in /data1/wangqiurui/code/datasets/rebuild/thumos/.
Combined file Diving.txt created in /data1/wangqiurui/code/datasets/rebuild/thumos/.
Combined file Shotput.txt created in /data1/wangqiurui/code/datasets/rebuild/thumos/.
Combined file JavelinThrow.txt created in /data1/wangqiurui/code/datasets/rebuild/thumos/.
Combined file BaseballPitch.txt created in /data1/wangqiurui/code/datasets/rebuild/thumos/.
Combined file CricketShot.txt created in /data1/wangqiurui/code/datasets/rebuild/thumos/.
Combined file Ambiguous.txt created in /data1/wangqiurui/code/datasets/rebuild/thumos/.
Combined file HammerThrow.txt created in /data1/wangqiurui/code/datasets/rebuild/thumos/.
Combined file CricketBowling.txt created in /data1/wangqiurui/code/datasets/rebuild/thumos/.
Combined file BasketballDunk.txt created in /data1/wangqiurui/code/datasets/rebuild/thumos/.
Combined f

## make it to json

In [7]:
import os
import json

def parse_file_to_dict(filepath):
    """解析单个文件并返回嵌套字典"""
    action_dict = {}
    with open(filepath, 'r') as file:
        for line in file:
            parts = line.strip().split()
            if len(parts) < 3:
                continue
            video_id, start_time, end_time = parts[0], float(parts[1]), float(parts[2])
            action_name = filepath.split('/')[-1].replace('.txt', '')
            if action_name not in action_dict:
                action_dict[action_name] = {}
            if video_id not in action_dict[action_name]:
                action_dict[action_name][video_id] = []
            action_dict[action_name][video_id].append((start_time, end_time))
    return action_dict

def convert_files_to_dict(directory):
    """遍历目录中的所有文件并构建嵌套字典"""
    complete_dict = {}
    for filename in os.listdir(directory):
        if filename.endswith('.txt'):
            filepath = os.path.join(directory, filename)
            file_dict = parse_file_to_dict(filepath)
            complete_dict.update(file_dict)
    return complete_dict

# 路径定义
output_dir = '/data1/wangqiurui/code/datasets/rebuild/thumos'

# 使用示例
action_data = convert_files_to_dict(output_dir)

# 如果需要，可以将字典保存为JSON文件
with open('action_data.json', 'w') as json_file:
    json.dump(action_data, json_file,indent=2)

print("Data has been parsed and saved.")


Data has been parsed and saved.


# convert an json to kv type

In [4]:
an = json.load(open('anet1.3_tsp_filtered.json', 'r'))

In [5]:
an['database']

{'sJFgo9H6zNo': {'duration': 139.042,
  'subset': 'training',
  'url': 'https://www.youtube.com/watch?v=sJFgo9H6zNo',
  'resolution': '640x360',
  'annotations': [{'segment': [0.01, 123.42336739937599],
    'label': 'Fun sliding down',
    'label_id': 57}]},
 'JDg--pjY5gg': {'duration': 126.178,
  'subset': 'validation',
  'url': 'https://www.youtube.com/watch?v=JDg--pjY5gg',
  'resolution': '1920x1080',
  'annotations': [{'segment': [61.420442338881465, 64.56014561469672],
    'label': 'Beer pong',
    'label_id': 10}]},
 'u2uoYvo8J5s': {'duration': 208.864,
  'subset': 'training',
  'url': 'https://www.youtube.com/watch?v=u2uoYvo8J5s',
  'resolution': '1280x720',
  'annotations': [{'segment': [127.33201508846798, 201.39247572684465],
    'label': 'Swinging at the playground',
    'label_id': 171}]},
 '0Gr4aKQzGYk': {'duration': 67.43,
  'subset': 'training',
  'url': 'https://www.youtube.com/watch?v=0Gr4aKQzGYk',
  'resolution': '1280x720',
  'annotations': [{'segment': [30.096653368

In [5]:
def transform_json(input_data):
    """转换JSON格式"""
    transformed_data = {}
    for video_id, video_info in input_data.items():
        video_id = 'v_' + video_id
        for annotation in video_info['annotations']:
            label = annotation['label']
            if label not in transformed_data:
                transformed_data[label] = {}
            if video_id not in transformed_data[label]:
                transformed_data[label][video_id] = []
            transformed_data[label][video_id].append(annotation['segment'])
    return transformed_data

# 示例输入数据
input_data = {
    'sJFgo9H6zNo': {
        'duration': 139.042,
        'subset': 'training',
        'url': 'https://www.youtube.com/watch?v=sJFgo9H6zNo',
        'resolution': '640x360',
        'annotations': [{
            'segment': [0.01, 123.42336739937599],
            'label': 'Fun sliding down',
            'label_id': 57
        },
        {
            'segment': [765, 999],
            'label': 'fuck',
            'label_id': 77
        }
        ]
    },
    'JDg--pjY5gg': {
        'duration': 126.178,
        'subset': 'validation',
        'url': 'https://www.youtube.com/watch?v=JDg--pjY5gg',
        'resolution': '1920x1080',
        'annotations': [{
            'segment': [61.420442338881465, 64.56014561469672],
            'label': 'Beer pong',
            'label_id': 10
        }]
    },
    'u2uoYvo8J5s': {
        'duration': 208.864,
        'subset': 'training',
        'url': 'https://www.youtube.com/watch?v=u2uoYvo8J5s',
        'resolution': '1280x720',
        'annotations': [{
            'segment': [127.33201508846798, 201.39247572684465],
            'label': 'Swinging at the playground',
            'label_id': 171
        }]
    }
}

# 转换格式
transformed_data = transform_json(an['database'])
print(transformed_data)

{'Fun sliding down': {'v_sJFgo9H6zNo': [[0.01, 123.42336739937599]], 'v_MYzG-TsW8w8': [[11.271747008580574, 21.60795399923478]], 'v_88qqQjRPFUQ': [[21.608548053627587, 25.616390485920526]], 'v_8kGiDHAnTqY': [[33.121001560062396, 98.54855382215287], [114.83757098283931, 118.63834165366613], [164.24758970358815, 174.021]], 'v_n2L9F6cMNaE': [[65.57153354134165, 79.02210452418097], [112.42294539781591, 135.0036224648986]], 'v_e9p0xmsU3h0': [[11.016689421200052, 105.19166147326608]], 'v_mwUP1yZQsh0': [[22.415738732993198, 30.63484432857513], [95.88956148137714, 129.76223908741179]], 'v_Nn4sVR3__DQ': [[19.897477133733105, 37.4827100388653]], 'v_-wWtZjqIH9o': [[0.2, 12.987631825273011]], 'v_jqYzz6YoMEY': [[30.143017160686426, 52.38629485179407]], 'v_ilE77hVgjjo': [[0.01, 109.881]], 'v_TxYZLJQOHvY': [[0.2, 3.3199797191887677], [18.50793291731669, 23.621464898595942]], 'v_QLsdBUBpz_8': [[18.922483619344774, 26.291335413416537]], 'v_aZQWCEejbk8': [[10.228382063134461, 21.65]], 'v_QR2BmWR5FGM': [

In [6]:
with open('an_transform.json', 'w') as json_file:
    json.dump(transformed_data, json_file,indent=2)

# charades transform

In [8]:
train = pd.read_csv('/data1/wangqiurui/code/datasets/charades/annotation/Charades_v1_train.csv')
test = pd.read_csv('/data1/wangqiurui/code/datasets/charades/annotation/Charades_v1_test.csv')

In [9]:

train.head()

id subject         scene  quality  relevance verified  \
0  46GP8    HR43       Kitchen      6.0        7.0      Yes   
1  N11GT    0KZ7        Stairs      6.0        7.0      Yes   
2  0IH69    6RE8       Bedroom      6.0        5.0      Yes   
3  KRF68    YA10  Laundry room      6.0        7.0      Yes   
4  MJO7C    6RE8       Kitchen      6.0        6.0      Yes   

                                              script                 objects  \
0  A person cooking on a stove while watching som...       food;stove;window   
1  One person opens up a folded blanket, then sne...     blanket;broom;floor   
2  A person is seen leaving a cabinet. They then ...  book;box;cabinet;shelf   
3  A person runs into their laundry room. They gr...      clothes;door;phone   
4  A person runs into their pantry holding a bott...               cup;phone   

                                        descriptions  \
0  A person cooks food on a stove before looking ...   
1  Person at the bottom of the staircase shakes a...   
2  A person is standing in a bedroom. They walk o...   
3  A person runs in and shuts door. The person gr...   
4  A person runs in place while holding a bottle ...   

                                             actions  length  
0                   c092 11.90 21.20;c147 0.00 12.60   24.83  
1  c098 8.60 14.20;c075 0.00 11.70;c127 0.00 15.2...   18.33  
2                                                NaN   30.25  
3  c018 22.60 27.80;c141 4.10 9.60;c148 10.30 25....   30.33  
4                    c015 0.00 32.00;c107 0.00 32.00   31.38

In [10]:
test.head()

id subject                                              scene  quality  \
0  YSKX3    CP6Y                                            Bedroom      5.0   
1  T5ECU    M7K8                                        Living room      6.0   
2  AAH6R    ENHU             Closet / Walk-in closet / Spear closet      6.0   
3  015XE    GFWE                                            Kitchen      6.0   
4  TJZ0P    ENHU  Home Office / Study (A room in a house used fo...      5.0   

   relevance verified                                             script  \
0        6.0      Yes   A person fixes the bed then throws pillow on it.   
1        7.0      Yes  One person is smiling and drinking while watch...   
2        6.0      Yes  A person undressing in the doorway walks to a ...   
3        5.0      Yes  A person is taking a picture of a light while ...   
4        7.0      Yes  A person in their home office opening a book t...   

                                           objects  \
0                      bed;blanket;mattress;pillow   
1                 chair;cup;dish;dog;vacuum;window   
2                     chair;clothes;doorway;mirror   
3                       camera;light;phone;picture   
4  arm;book;chair;food;sandwich;shelf;table;window   

                                        descriptions  \
0  A person looks under a mattress and pats the b...   
1  A person leaves the room holding an umbrella w...   
2  A person is looking in the mirror, adjusting h...   
3  A person holds a camera up to a light on the c...   
4  A person sitting down picks up a book. A perso...   

                                             actions  length  
0  c077 12.10 18.00;c079 11.80 17.30;c080 13.00 1...   16.62  
1  c137 0.30 9.00;c092 0.00 18.90;c152 3.50 31.00...   31.29  
2  c059 3.50 8.00;c151 3.00 7.60;c148 0.00 8.00;c...    7.38  
3  c015 0.00 32.10;c087 0.60 32.10;c016 0.00 32.1...   32.83  
4  c067 8.60 13.80;c028 6.90 11.90;c059 0.00 19.0...   17.71

In [11]:
train.shape,test.shape

((7985, 11), (1863, 11))

In [12]:
# map the action classes to the action name
with open('/data1/wangqiurui/code/datasets/charades/annotation/Charades_v1_classes.txt', 'r') as f:
    lines = f.readlines()
    charades_classes = {}
    for line in lines:
        parts = line.strip().split(' ')
        charades_classes[parts[0]] = ' '.join(parts[1:])

In [13]:
charades_classes 

{'c000': 'Holding some clothes',
 'c001': 'Putting clothes somewhere',
 'c002': 'Taking some clothes from somewhere',
 'c003': 'Throwing clothes somewhere',
 'c004': 'Tidying some clothes',
 'c005': 'Washing some clothes',
 'c006': 'Closing a door',
 'c007': 'Fixing a door',
 'c008': 'Opening a door',
 'c009': 'Putting something on a table',
 'c010': 'Sitting on a table',
 'c011': 'Sitting at a table',
 'c012': 'Tidying up a table',
 'c013': 'Washing a table',
 'c014': 'Working at a table',
 'c015': 'Holding a phone/camera',
 'c016': 'Playing with a phone/camera',
 'c017': 'Putting a phone/camera somewhere',
 'c018': 'Taking a phone/camera from somewhere',
 'c019': 'Talking on a phone/camera',
 'c020': 'Holding a bag',
 'c021': 'Opening a bag',
 'c022': 'Putting a bag somewhere',
 'c023': 'Taking a bag from somewhere',
 'c024': 'Throwing a bag somewhere',
 'c025': 'Closing a book',
 'c026': 'Holding a book',
 'c027': 'Opening a book',
 'c028': 'Putting a book somewhere',
 'c029': 'Smil

In [14]:
def transform_charades(df,action_classes):
    """转换Charades数据集为字典"""
    for i in range(df.shape[0]):
        vn = df.loc[i, 'id']
        actions = df.loc[i, 'actions']
        try:
            inf = actions.split(';')
            for j in range(len(inf)):
                action = inf[j].split(' ')
                an = charades_classes[action[0]]
                if an not in action_classes:
                    action_classes[an] = {}
                if vn not in action_classes[an]:
                    action_classes[an][vn] = []
                action_classes[an][vn].append([float(action[1]), float(action[2])])
        except Exception as e:
            print(actions)
            print(vn)
            print(e)
            continue
    return action_classes


In [15]:
action_classes = {}
action_classes = transform_charades(train,action_classes)
action_classes = transform_charades(test,action_classes)

nan
0IH69
'float' object has no attribute 'split'
nan
PY5M4
'float' object has no attribute 'split'
nan
4ZNNP
'float' object has no attribute 'split'
nan
D4CHP
'float' object has no attribute 'split'
nan
B9YPQ
'float' object has no attribute 'split'
nan
003WS
'float' object has no attribute 'split'
nan
JNLCW
'float' object has no attribute 'split'
nan
8HLKN
'float' object has no attribute 'split'
nan
07E49
'float' object has no attribute 'split'
nan
XPY4P
'float' object has no attribute 'split'
nan
MJPET
'float' object has no attribute 'split'
nan
3P2U4
'float' object has no attribute 'split'
nan
BXL9D
'float' object has no attribute 'split'
nan
1B2QD
'float' object has no attribute 'split'
nan
FBL47
'float' object has no attribute 'split'
nan
5VGLI
'float' object has no attribute 'split'
nan
YRIBO
'float' object has no attribute 'split'
nan
8GRE9
'float' object has no attribute 'split'
nan
9ALI5
'float' object has no attribute 'split'
nan
5EFQ7
'float' object has no attribute 'split'


In [16]:
action_classes

{'Watching/Looking outside of a window': {'46GP8': [[11.9, 21.2]],
  'MD41D': [[11.0, 37.7]],
  'U1DTW': [[21.8, 34.0]],
  '5ACD3': [[3.0, 30.0]],
  'S72J9': [[15.5, 26.2]],
  'XV8CH': [[22.4, 29.0]],
  'MJX48': [[1.0, 6.4]],
  'YORQM': [[16.9, 25.0]],
  '19PNV': [[0.0, 17.6]],
  'YUEB9': [[21.0, 29.4]],
  'E23CT': [[0.0, 5.0]],
  'HDX87': [[0.7, 29.0]],
  '8RSZ4': [[1.9, 12.7]],
  'NMGIV': [[0.0, 15.5]],
  'R08G9': [[13.4, 33.0]],
  '0CX32': [[18.4, 34.0]],
  'X0O65': [[19.5, 25.9]],
  'UY7BK': [[18.1, 29.3]],
  'Y2PNC': [[7.9, 32.0]],
  'S8TI7': [[2.3, 9.5]],
  'II0EJ': [[14.7, 31.0]],
  'UPZJ5': [[2.3, 10.1]],
  '406LH': [[21.3, 31.1]],
  'Y9JWG': [[1.5, 8.0]],
  'OXPD4': [[0.0, 25.1]],
  '1RNK6': [[0.0, 5.0]],
  'P76PG': [[0.0, 38.0]],
  '1HL2K': [[0.0, 6.0]],
  'VXRCZ': [[0.0, 11.6]],
  'VU4J8': [[0.0, 29.0]],
  '8DQ3V': [[0.0, 13.5]],
  '72VBG': [[6.7, 17.4]],
  'DG5TX': [[0.0, 24.8]],
  '3V7MT': [[0.0, 3.7]],
  'X89FW': [[0.0, 18.2]],
  'CLORP': [[14.6, 24.4]],
  'Q7G9N': [[5.3,

In [17]:
with open('charades_transform.json', 'w') as json_file:
    json.dump(action_classes, json_file,indent=2)

In [18]:
len(action_classes.keys())

157

# conbine three jsons

In [19]:
an = json.load(open('an_transform.json', 'r'))
ch = json.load(open('charades_transform.json', 'r'))
thu = json.load(open('action_data.json', 'r'))

In [28]:
s = {0:'an',1:'ch',2:'thu'}

In [29]:
# combine the three datasets
combined = {}
for idx,d in enumerate([an, ch, thu]):
    for k, v in d.items():
        if k not in combined:
            combined[k] = {}
        v.update({'subset': s[idx]})
        combined[k].update(v)

In [31]:
# 157 + 200 + 20 = 377
len(combined.keys())

377

In [32]:
combined['Watching/Looking outside of a window']['subset']

'ch'

In [33]:
with open('combined.json', 'w') as json_file:
    json.dump(combined, json_file,indent=2)

# check combined data and decide how to rebuild

In [12]:
al = json.load(open('combined.json', 'r'))

In [ ]:
import cv2
video_lengths = {}

# 假设所有视频文件都在 "videos" 目录下
video_directory = "videos"
for category, videos in al.items():
    for video_id in videos:
        video_path = os.path.join(video_directory, video_id + ".mp4")
        if video_id == 'subset':
            continue
        if os.path.exists(video_path):
            cap = cv2.VideoCapture(video_path)
            if cap.isOpened():
                fps = cap.get(cv2.CAP_PROP_FPS)
                frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
                duration = frame_count / fps
                if video_id not in video_lengths:
                    video_lengths[video_id] = {}
                video_lengths[video_id]['duration'] = duration
                video_lengths[video_id]['frames'] = frame_count
            cap.release()
            print(f"{video_id} duration: {duration:.2f} seconds, frames: {frame_count}")
        else:
            print(f"Warning: {video_path} does not exist.")

In [46]:
with open(("video_lengths.json"), "w") as f:
    json.dump(video_lengths, f, indent=4)

In [11]:
video_lengths = json.load(open('video_lengths.json', 'r'))

In [ ]:
background_segments = {}

for category, videos in al.items():
    for video_id, segments in videos.items():
        if video_id == 'subset':
            continue
        try:
            total_length = video_lengths.get(video_id, 0)['duration']  # 使用获取到的视频长度
            points = [0]
            for segment in segments:
                points.extend(segment)
            points.append(total_length)
            
            bg_segments = []
            for i in range(0, len(points), 2):
                start = points[i]
                end = points[i+1]
                if start != end and end - start > 2:
                    bg_segments.append([start, end])
                else:
                    print(f"Invalid segment: {end} - {start}")
            if len(bg_segments) > 0:
                background_segments[video_id] = bg_segments
        except Exception as e:
            print(video_id)
            print(e)

print(background_segments)

In [59]:
with open('background_segments_filter2s.json', 'w') as json_file:
    json.dump(background_segments, json_file,indent=4)

In [24]:
background_segments = json.load(open('background_segments.json', 'r'))

In [22]:
len(background_segments.keys()),len(al.keys())

(24950, 377)

In [28]:
len(background_segments.keys()),len(al.keys())

(22770, 377)

In [60]:
len(background_segments.keys()),len(al.keys())

(22260, 377)

In [70]:
vn = []
for c in al.keys():
    for v in al[c].keys():
        if v not in vn:
            vn.append(v)

In [71]:
len(vn)

24951

In [73]:
len(json.load(open('/data1/wangqiurui/code/datasets/rebuild/anet1.3_tsp_filtered.json', 'r'))['database'].keys())

14913

In [74]:
len(json.load(open('/data1/wangqiurui/code/datasets/rebuild/v1-3.json', 'r'))['database'].keys())

19994

In [72]:
bn = random.choice(list(background_segments.keys()))
print(bn)
seg = random.choice(background_segments[bn])
seg

v_224E-VtB4k4


[103.77417937533828, 108.69905568467637]

In [77]:
vc = random.choice(list(al.keys()))
print(vc)
vn = random.choice(list(al[vc].keys()))
print(vn)
seg = random.choice(al[vc][vn])
seg

Skiing
v_BOOX9aGlSEs


[45.54079944763897, 56.64215770309068]

# build videos contain 1,3,5,7,9,15,20,30 instances

In [45]:
al = json.load(open('combined.json', 'r'))

In [54]:
for k,v in al.items():
    for vn,ss in v.items():
        if vn == 'subset':
            continue
        if ss == []:
                print(vn,":",ss)
        
        for s in ss:
            if s == []:
                print(vn,":",ss)
            if s[1] - s[0] < 2:
                print(vn,":",ss)

v_f-JfdEfNQlE : []
v_uKzelWWaYB4 : []
v_P3kWD8Oocio : []
v_RD7AUdgtchE : []
v_c1Gby2EHBzs : []
v_re4vD9S8ThA : []
v_SGiMk9KdOQw : []
v__xgGaxc1jNE : []
v_OZftVCeblMk : []
v_h7iCyiNUxeE : []
v_qMJi2nXWOkg : []
v_L36MIRUpcrI : []
v_z9uVyf0D8eM : []
v_IsHM24qWmpI : []
v_HCphw9_Jku8 : []
v_vMdSEzQkRTg : []
v_DzCk5xjSF9o : []
v_pRGlbeqRfM0 : []
v_76RoR_LbIzQ : []
v_ggw-70xi0dA : []
v_iDofsMwceTo : []
v_CBN0dqyWB7w : []
v_Kkkrap77n5M : []
v_5qBzjfW-sMs : []
v_ripbruSSD8w : []
v_gvHcfC9snJA : []
v_hwGvU9Csz98 : []
v_xld0M1MXNiE : []
v_74AJ-1e1qGA : []
v_SLdf2ZUdgEQ : []
v_9T1C2CW_P0A : []
v_q8c_0JTe5r8 : []
v_mtQUYdj2Ecg : []
v_T_5ANYuDWOA : []
v_kBUDMFgWO9I : []
v_a7DEFV0_nCE : []
v_gB_xHRJY7sw : []
v_hDb19ih3jAA : []
v_wb8TkqxxEuo : []
v_MWWDqMI-rxU : []
v_4S5ethZhgqs : []
v_uzXbaoWOm5o : []
v_j55LAXY-T0E : []
v_ZKo3_ifK2tQ : []
v_XFlWVBU4z9E : []
v_k74CgBa46bA : []
v_wZJeEV6sZXE : []
v_NNZKinEXYc4 : []
v_BtYKJOmw-aU : []
v_6RePzOd3GvQ : []
v_ehGHCYKzyZ8 : []
v_2uMG44uNDJ8 : []
v_Ocd1VWIIeV

In [50]:
for k, v in al.items():
    for vn, ss in v.items():
        if vn == 'subset':
            continue
        items_to_remove = []
        for s in ss:
            if s[1] - s[0] < 2:
                print(vn, ":", ss)
                items_to_remove.append(s)
        for item in items_to_remove:
            ss.remove(item)
        v[vn] = ss  # Update the dictionary with the modified list

# Note: No need to update 'al' since 'v' is a reference to the same dictionary.


v_0MyaFtXcTKI : [[47.587113884555386, 49.6265616224649], [54.385273010920436, 62.88297191887675], [72.06048673946958, 77.83892199687988], [79.8783697347894, 90.41551638065522], [102.65220280811232, 104.35174258970359], [113.52925741029641, 118.6278767550702], [164.17554290171608, 169.27416224648985], [179.1479360374415, 185.60678003120125], [197.16471138845554, 200.90404212168488]]
v_f-JfdEfNQlE : [[51.00614416957631, 52.93753000732274]]
v_b8pCuIPzb3o : [[4.67998004818152, 8.59810287921721], [19.19154650169095, 20.279913978157357], [26.737561005191363, 32.687303209874386], [37.984024928677556, 40.37843337690365]]
v_uKzelWWaYB4 : [[0.01, 0.02]]
v_P3kWD8Oocio : [[4.628823442674115, 6.288814887700485]]
v_m1pNOYN-DoI : [[3.3259408871441267, 8.368498907760356], [16.415134047041573, 17.70259566932657], [26.82211500365442, 28.109576602410254], [34.97603846244136, 41.62792338934649]]
v_m1pNOYN-DoI : [[3.3259408871441267, 8.368498907760356], [16.415134047041573, 17.70259566932657], [26.82211500

In [43]:
keys_to_delete = []

for k, v in al.items():
    for vn, ss in v.items():
        if vn == 'subset':
            continue
        for s in ss:
            if s[1] <= s[0]:
                keys_to_delete.append((k, vn))
                print(vn, ":", ss)

# Now delete the keys
for k, vn in keys_to_delete:
    del al[k][vn]


v_6kgJx6ahgq0 : [[0, 0]]
v_e6J_ygZ779A : [[142.281, 142.281]]
v_QhiKgeJV3k0 : [[4.10395084399376, 4.10395084399376], [29.335648625585023, 170.99795183307336]]


In [56]:
keys_to_delete = []

for k, v in al.items():
    for vn, ss in v.items():
        if vn == 'subset':
            continue
        if ss == []:
            print(vn,":",ss)
            keys_to_delete.append((k, vn))
        
        for s in ss:
            if s[1] <= s[0]:
                keys_to_delete.append((k, vn))
                print(vn, ":", ss)

# Now delete the keys
for k, vn in keys_to_delete:
    del al[k][vn]


In [57]:
with open('combined.json', 'w') as json_file:
    json.dump(al, json_file,indent=2)

In [3]:
background_segments = json.load(open('background_segments_filter2s.json', 'r'))

In [12]:
for k,v in background_segments.items():
    for s in v:
        if s[1] < s[0]:
            print(k,s)

## change resolution

## rebuild one instance (one action,one or two background) 10 samples per action class

In [4]:
bn = random.choice(list(background_segments.keys()))
print(bn)
bg = random.choice(background_segments[bn])
bg

4ZJXR


[33.0, 31.7]

In [8]:
vc = random.choice(list(al.keys()))
print(vc)
vn = random.choice(list(al[vc].keys()))
print(vn)
ac = random.choice(al[vc][vn])
ac

Putting a sandwich somewhere
D6D85


[1.9, 6.7]

In [ ]:
n = 1
combinations = [
    (['bg', 'ac', 'bg'], 2),  # Sequence and count of background clips
    (['ac', 'bg', 'bg'], 2),
    (['bg', 'bg', 'ac'], 2)
]
combinations_2 = [
    (['bg', 'ac'], 1),
    (['ac', 'bg'], 1),
]

anno_json = {}
for vc in al.keys():
    for i in range(10):
        # action
        vn = random.choice(list(al[vc].keys()))
        ac = random.choice(al[vc][vn])
        action_cap = cv2.VideoCapture('resized_videos/' + vn + '.mp4')
        fps = action_cap.get(cv2.CAP_PROP_FPS)
        start_frame = int(ac[0] * fps)
        end_frame = int(ac[1] * fps)
        action_cap.set(cv2.CAP_PROP_POS_FRAMES, start_frame)
        ac_buffer = []
        for j in range(start_frame, end_frame):
            ret, frame = action_cap.read()
            if not ret:
                break
            ac_buffer.append(frame)
        ac_buffer = np.stack(ac_buffer)
        
        # background
        number_of_background = random.choices([1,2],weights=[0.5,0.5])
        bgs_buffer = []
        for nb in range(number_of_background[0]):
            bn = random.choice(list(background_segments.keys()))
            bg = random.choice(background_segments[bn])
            bg_cap = cv2.VideoCapture('resized_videos/' + bn + '.mp4')
            fps = bg_cap.get(cv2.CAP_PROP_FPS)
            start_frame = int(bg[0] * fps)
            end_frame = int(bg[1] * fps)
            bg_cap.set(cv2.CAP_PROP_POS_FRAMES, start_frame)
            bg_buffer = []
            for j in range(start_frame, end_frame):
                ret, frame = bg_cap.read()
                if not ret:
                    break
                bg_buffer.append(frame)
            bg_buffer = np.stack(bg_buffer)
            bgs_buffer.append(bg_buffer)
        
        # combine, random [bg,ac,bg] [bg,ac] [ac,bg] [ac,bg,bg] [bg,bg,ac]
        if len(bgs_buffer) == 2:
        # Randomly select a combination
            chosen_combo, bg_count = random.choice(combinations)
        else:
            chosen_combo, bg_count = random.choice(combinations_2)
        combined_buffer = []

        # Combine the sequences based on the chosen combination
        bg_index = 0
        start_frames = 0
        end_frames = 0
        for segment in chosen_combo:
            if segment == 'ac':
                # Add action frames
                combined_buffer.extend(ac_buffer)
                end_frames = start_frames + ac_buffer.shape[0]
            elif segment == 'bg':
                if bg_index < len(bgs_buffer):
                    # Add background frames
                    combined_buffer.extend(bgs_buffer[bg_index])
                    start_frames = start_frames + bgs_buffer[bg_index].shape[0]
                    bg_index += 1
            
        output_video_directory = "rebuild_videos"
        if not os.path.exists(output_video_directory):
            os.makedirs(output_video_directory)

        # 输出视频文件路径
        output_video_path = os.path.join(output_video_directory, f'{n}.mp4')

        # 视频写入器设置
        fps = 30
        frame_size = (1280, 720)
        fourcc = cv2.VideoWriter_fourcc(*'mp4v')
        out = cv2.VideoWriter(output_video_path, fourcc, fps, frame_size)

        # 假设 combined_buffer 是包含所有视频帧的列表
        for frame in combined_buffer:
            out.write(frame)  # 写入帧到输出视频

        # 释放视频写入器资源
        out.release()

        print(f"Video successfully saved to {output_video_path}")

        anno_json[n] = {'seg':[start_frames/fps,end_frames/fps],'ac':vc}

        n = n + 1

# save json
with open('annotation.json','r') as f:
    json.dump(anno_json,f,indent=2)
            

## rebuild three instances (two background clips( babaa,baaba,baaab,bbaaa,ababa,abaab,abbaa,aabab,aabba,aaabb ) )

### keep 10 samples per action class, random choice another 2 classes and bg clips

# summarize
1, convert all dataset annotations to key(action classes), value(video name : action segments) type, combine them and save as json

2, compute the background segments according to the converted annotations, and save as key(video name), value(background segments) type

3, put all videos together and change the resolution to 1280x720

4, grenate videos which has different numbers of action instances

In [10]:
import itertools

def generate_combinations(num_a, num_b):
    # 生成所有可能的组合
    total_length = num_a + num_b
    patterns = ['a', 'b']
    all_combinations = itertools.product(patterns, repeat=total_length)
    
    valid_combinations = []
    # 筛选出具有正确数量的 'a' 和 'b' 的组合
    for combination in all_combinations:
        if combination.count('a') == num_a and combination.count('b') == num_b:
            valid_combinations.append(''.join(combination))
    
    return valid_combinations

# 生成 5个动作片段和 4个背景片段的所有组合
combinations_5_4 = generate_combinations(5, 4)
print("5 'a's and 4 'b's combinations:", combinations_5_4)

# 生成 7个动作片段和 6个背景片段的所有组合
combinations_7_6 = generate_combinations(7, 6)
print("7 'a's and 6 'b's combinations:", combinations_7_6)

# 生成 9个动作片段和 8个背景片段的所有组合
combinations_9_8 = generate_combinations(9, 8)
print("9 'a's and 8 'b's combinations:", combinations_9_8)

combinations_30_15 = generate_combinations(30, 15)
print("30 'a's and 15 'b's combinations:", lenn(combinations_30_15))


5 'a's and 4 'b's combinations: ['aaaaabbbb', 'aaaababbb', 'aaaabbabb', 'aaaabbbab', 'aaaabbbba', 'aaabaabbb', 'aaabababb', 'aaababbab', 'aaababbba', 'aaabbaabb', 'aaabbabab', 'aaabbabba', 'aaabbbaab', 'aaabbbaba', 'aaabbbbaa', 'aabaaabbb', 'aabaababb', 'aabaabbab', 'aabaabbba', 'aababaabb', 'aabababab', 'aabababba', 'aababbaab', 'aababbaba', 'aababbbaa', 'aabbaaabb', 'aabbaabab', 'aabbaabba', 'aabbabaab', 'aabbababa', 'aabbabbaa', 'aabbbaaab', 'aabbbaaba', 'aabbbabaa', 'aabbbbaaa', 'abaaaabbb', 'abaaababb', 'abaaabbab', 'abaaabbba', 'abaabaabb', 'abaababab', 'abaababba', 'abaabbaab', 'abaabbaba', 'abaabbbaa', 'ababaaabb', 'ababaabab', 'ababaabba', 'abababaab', 'ababababa', 'abababbaa', 'ababbaaab', 'ababbaaba', 'ababbabaa', 'ababbbaaa', 'abbaaaabb', 'abbaaabab', 'abbaaabba', 'abbaabaab', 'abbaababa', 'abbaabbaa', 'abbabaaab', 'abbabaaba', 'abbababaa', 'abbabbaaa', 'abbbaaaab', 'abbbaaaba', 'abbbaabaa', 'abbbabaaa', 'abbbbaaaa', 'baaaaabbb', 'baaaababb', 'baaaabbab', 'baaaabbba', 'baaa

: 

In [4]:
len(combinations_5_4),len(combinations_7_6),len(combinations_9_8)

(126, 1716, 24310)

In [9]:
import random
random.choices(combinations_9_8,weights=[1/len(combinations_9_8)]*len(combinations_9_8))[0]

'baabbabbbbabaaaaa'